# ΟΜΑΔΑ 43

### Κορακοβούνης Δημήτριος     -    Α.Μ. 03116692
### Αναγνωστόπουλος Θεόδωρος   -    Α.Μ. 03116066

# Παιχνίδι

Το παιχνίδι για την ομάδα 43 είναι το Krull

<br><br>

# Παίζοντας Atari με βαθιά ενισχυτική μάθηση

Προσοχή: για να μπορέσει να τρέξει αυτό το notebook στο Kaggle πρέπει να ενεργοποιήσετε το Internet και την GPU για τον πυρήνα σας. Αυτό απαιτεί την επιβεβαίωση του κινητού σας με SMS. Πηγαίντε στο δεξί sidebar στα settings και θα το δείτε. 

Τελικά πρέπει να έχετε αυτή την εικόνα:

![](https://i.imgur.com/Ek5hOIo.jpg)

## Tensorboard και ngrok

Αντικαταστήστε το authentication token σας που παίρνετε από το [ngrok](https://ngrok.com/) στη γραμμή που υποδεικνύεται. Όταν εκτελεστεί το κελί θα σας δώσει το URL όπου μπορείτε να βλέπετε το TensorBoard. Σημειώστε ότι σε περίπτωση επανεκκίνησης του πυρήνα θα πρέπει να ξανατρέξετε το κελί. Η διεύθυνση θα είναι διαφορετική, αλλά τα προηγούμενα στατιστικά σας δεν χάνονται (μέχρι να ανακυκλωθεί ο πυρήνας).

In [1]:
!apt install apt-utils psmisc -y
!killall -9 ngrok
!rm -rf *ngrok*
!wget https://bin.equinox.io/c/4VmDzA7iaHb/ngrok-stable-linux-amd64.zip
!unzip ngrok-stable-linux-amd64.zip
!mkdir -p ngrok-dir
!mv ngrok ngrok-dir/



Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following additional packages will be installed:
  apt libapt-pkg5.0
Suggested packages:
  apt-doc aptitude | synaptic | wajig
The following NEW packages will be installed:
  apt-utils psmisc
The following packages will be upgraded:
  apt libapt-pkg5.0
2 upgraded, 2 newly installed, 0 to remove and 25 not upgraded.
Need to get 2267 kB of archives.
After this operation, 1053 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu bionic-updates/main amd64 libapt-pkg5.0 amd64 1.6.12ubuntu0.2 [806 kB]
Get:2 http://archive.ubuntu.com/ubuntu bionic-updates/main amd64 apt amd64 1.6.12ubuntu0.2 [1201 kB]
Get:3 http://archive.ubuntu.com/ubuntu bionic-updates/main amd64 apt-utils amd64 1.6.12ubuntu0.2 [207 kB]
Get:4 http://archive.ubuntu.com/ubuntu bionic-updates/main amd64 psmisc amd64 23.1-1ubuntu0.1 [52.5 kB]
Fetched 2267 kB in 1s (2264 kB/s) 
debconf: delaying package

In [2]:
# Στην επόμενη γραμμή βάλτε το δικό σας authentication token από το ngrok
!ngrok-dir/ngrok authtoken 1pSIjwmB6IAFISnVyCvlchN8ir0_6FQwStz7xNugGnvVwVCx3

LOG_DIR = 'tb_log/'
!mkdir -p LOG_DIR

get_ipython().system_raw(
    'tensorboard --logdir {} --host 0.0.0.0 --port 6006 &'
    .format(LOG_DIR)
)
get_ipython().system_raw('ngrok-dir/ngrok http 6006 &')
! curl -s http://localhost:4040/api/tunnels | python3 -c \
    "import sys, json; print(json.load(sys.stdin)['tunnels'][0]['public_url'])"
print("Wait 10-15 seconds and then click the URL above to open TensorBoard")

Authtoken saved to configuration file: /root/.ngrok2/ngrok.yml
http://bdfd39cc553c.ngrok.io
Wait 10-15 seconds and then click the URL above to open TensorBoard


## Εγκατάσταση βιβλιοθήκης και gym

In [3]:
!pip install --upgrade pip
!pip install --upgrade stable_baselines3[extra]
# we need a specific version of gym because of this issue: https://github.com/DLR-RM/stable-baselines3/issues/294
!pip install gym==0.17.3
!pip install sb3-contrib


from stable_baselines3.common.env_util import make_atari_env
from stable_baselines3.common.vec_env import VecFrameStack
from stable_baselines3.common.evaluation import evaluate_policy


# Reinforcement Learning Algorithms
from stable_baselines3 import DQN
from stable_baselines3 import A2C
from stable_baselines3 import PPO
from stable_baselines3 import TD3
from sb3_contrib import QRDQN

import datetime # For filenames while logging
import joblib

     |████████████████████████████████| 152 kB 4.3 MB/s eta 0:00:01
     |████████████████████████████████| 2.8 MB 27.7 MB/s eta 0:00:01
     |████████████████████████████████| 1.6 MB 4.3 MB/s eta 0:00:01
  Created wheel for gym: filename=gym-0.17.3-py3-none-any.whl size=1654653 sha256=cccace6e55a8fd07db19a9b8e9f397acbb2ff9a88b4d2b1be0b454d9549e64c2
  Stored in directory: /root/.cache/pip/wheels/d1/81/4b/dd9c029691022cb957398d1f015e66b75e37637dda61abdf58
Successfully built gym


  Attempting uninstall: gym
    Found existing installation: gym 0.18.0
    Uninstalling gym-0.18.0:
      Successfully uninstalled gym-0.18.0
     |████████████████████████████████| 104 kB 6.4 MB/s eta 0:00:01
     |████████████████████████████████| 1.9 MB 31.9 MB/s eta 0:00:01
     |████████████████████████████████| 2.8 MB 46.0 MB/s eta 0:00:01
     |████████████████████████████████| 242 kB 55.2 MB/s eta 0:00:01


     |████████████████████████████████| 107 kB 52.1 MB/s eta 0:00:01
     |████████████████████████████████| 89 kB 7.7 MB/s  eta 0:00:01
     |████████████████████████████████| 121 kB 56.0 MB/s eta 0:00:01
     |████████████████████████████████| 96 kB 5.7 MB/s  eta 0:00:01
     |████████████████████████████████| 90 kB 9.2 MB/s  eta 0:00:01
     |████████████████████████████████| 93 kB 2.0 MB/s  eta 0:00:01
     |████████████████████████████████| 84 kB 3.9 MB/s  eta 0:00:01
     |████████████████████████████████| 55 kB 3.2 MB/s  eta 0:00:01
  Created wheel for pytest-env: filename=pytest_env-0.6.2-py3-none-any.whl size=2370 sha256=4fcb0a9e814cc8d9369b0d851c27549096d8e1f2cbf73250cc4c17d1cb8b5840
  Stored in directory: /root/.cache/pip/wheels/00/78/6f/8413b85149939cd491ef2c5d3c5422e49cb2f898c8402f81f7
  Created wheel for importlab: filename=importlab-0.6.1-py2.py3-none-any.whl size=21288 sha256=3211eaadf00898132362a0658450aebde6f16e4fe5dedb4f24e275e8542c0fdc
  Stored in directory: /root/.

## Τυχαίος πράκτορας

Παρακάτω ορίζουμε έναν τυχαίο πράκτορα και καταγράφουμε το σκορ όταν αυτός χάνει. 
Επαναλαμβάνουμε 10 φορές και υπολογίζουμε το μέσο σκορ

In [24]:
import numpy as np
import gym
env = gym.make('KrullDeterministic-v4')
obs = env.reset()
mean_reward = 0
for _ in range(10):
    obs = env.reset()
    sum = 0
    while(True):
        # Random action
        action = env.action_space.sample()
        obs, reward, done, info = env.step(action)
        sum += reward
        if done:
            break
    print(sum)
    mean_reward += sum
mean_reward = mean_reward / 10.0
print(f"\nEval reward: {mean_reward}")

2013.0
1380.0
706.0
1368.0
1716.0
1692.0
1164.0
1932.0
2100.0
1071.0

Eval reward: 1514.2


#### Αποτέλεσμα
Παρατηρούμε το μέσο σκορ να είναι κοντά στο 1500

### Ορισμός Βοηθητικών συναρτήσεων

Παρακάτω ορίζονται οι συναρτήσεις διαχείρησης των μοντέλω - Δημιουργία, Εκπαίδευση, Εμφάνιση, Αποθήκευση

Χρησιμοποιήθηκαν 4 πιθανές αρχιτεκτονικές προς εκπαίδευση που αναμένεται να δώσουν καλά αποτελέσματα, τα DQN, A2C, PPO και QRDQN

In [14]:
def construct_enviroment(game_type,n_envs=1):
    atari_env="Krull"+game_type
    env = make_atari_env(atari_env, n_envs=n_envs, seed=0)
    env = VecFrameStack(env, n_stack=4)
    test_env = make_atari_env(atari_env, n_envs=1, seed=0)
    test_env = VecFrameStack(test_env, n_stack=4)
    return env,test_env



def construct_rl_model(algorithm,game_type, policy, n_envs=1):
    model_name = algorithm + '-' + game_type + '-' + policy 
    time_stamp=datetime.datetime.now().strftime("-%Y%m%d-%H%M%S")
    model_log= LOG_DIR + model_name + time_stamp
    env,test_env = construct_enviroment(game_type,n_envs)
    if algorithm == 'DQN':
        model = DQN(policy, env, verbose=1, tensorboard_log=model_log, buffer_size=100000)
        return model,test_env, model_name
    elif algorithm == 'A2C':
        model = A2C(policy, env, verbose=1, tensorboard_log=model_log)
        return model,test_env, model_name
    elif algorithm== 'PPO':
        model = PPO(policy, env, verbose=1, tensorboard_log=model_log)
        return model,test_env, model_name
    elif algorithm== 'QRDQN':
        model = QRDQN(policy, env, verbose=1, tensorboard_log=model_log, buffer_size=100000)
        return model,test_env, model_name 
    else:
        print("Invalid Input")
    
    
def evaluate_model(train_model,test_env, model_name,scores_dict):
    mean_reward, std_reward = evaluate_policy(train_model, test_env, n_eval_episodes=5)
    scores_dict[model_name+'_mean_reward'] = mean_reward
    scores_dict[model_name+'_std_reward'] = std_reward
    print(f"Eval reward: {mean_reward} (+/-{std_reward})")
    

    
def learn_eval_save_model(algorithm,game_type, policy, scores_dict,n_env=1, max_steps = 1000): 
    model, test_env,model_name = construct_rl_model(algorithm,game_type,policy, n_env)
    train_model = model.learn(total_timesteps=max_steps)
    print("Finished training "+model_name)
    evaluate_model(train_model,test_env, model_name,scores_dict)
    print("Finished evaluating "+model_name)
    train_model.save(model_name)
    print("Saved model:"+model_name)

Στο ακόλουθο κελί φορτώνουμε από το dropbox τα μοντέλα που έχουμε εκπαιδεύσει 

In [5]:
!wget --no-check-certificate 'https://www.dropbox.com/s/i33937mq2rs0fcm/A2C-Deterministic-v4-CnnPolicy.zip?dl=1' -O A2C-Deterministic-v4-CnnPolicy.zip
!wget --no-check-certificate 'https://www.dropbox.com/s/yxlvbkk61i6c2a5/A2C--v4-CnnPolicy.zip?dl=1' -O A2C--v4-CnnPolicy.zip
!wget --no-check-certificate 'https://www.dropbox.com/s/p1v7jd7q2n4clwl/A2C-NoFrameskip-v4-CnnPolicy.zip?dl=1' -O A2C-NoFrameskip-v4-CnnPolicy.zip
!wget --no-check-certificate 'https://www.dropbox.com/s/j38znq5vhxybqvh/DQN-Deterministic-v4-CnnPolicy.zip?dl=1' -O DQN-Deterministic-v4-CnnPolicy.zip
!wget --no-check-certificate 'https://www.dropbox.com/s/0z9x4eze2zk00b9/DQN--v4-CnnPolicy.zip?dl=1' -O DQN--v4-CnnPolicy.zip
!wget --no-check-certificate 'https://www.dropbox.com/s/la870jz3hq9und1/DQN-NoFrameskip-v4-CnnPolicy.zip?dl=1' -O DQN-NoFrameskip-v4-CnnPolicy.zip
!wget --no-check-certificate 'https://www.dropbox.com/s/dfnv49sqdfrvbjn/PPO-Deterministic-v4-CnnPolicy.zip?dl=1' -O PPO-Deterministic-v4-CnnPolicy.zip
!wget --no-check-certificate 'https://www.dropbox.com/s/e1xw3drirmhv1wj/PPO--v4-CnnPolicy.zip?dl=1' -O PPO--v4-CnnPolicy.zip
!wget --no-check-certificate 'https://www.dropbox.com/s/rbbeg1k3k5uccmd/PPO-NoFrameskip-v4-CnnPolicy.zip?dl=1' -O PPO-NoFrameskip-v4-CnnPolicy.zip
!wget --no-check-certificate 'https://www.dropbox.com/s/0q9ih6g7sbtsvr5/QRDQN-Deterministic-v4-CnnPolicy.zip?dl=1' -O QRDQN-Deterministic-v4-CnnPolicy.zip
!wget --no-check-certificate 'https://www.dropbox.com/s/v7nyxfgndwmav18/QRDQN--v4-CnnPolicy.zip?dl=1' -O QRDQN--v4-CnnPolicy.zip
!wget --no-check-certificate 'https://www.dropbox.com/s/nl7wes4vi1iefl9/QRDQN-NoFrameskip-v4-CnnPolicy.zip?dl=1' -O QRDQN-NoFrameskip-v4-CnnPolicy.zip


--2021-03-14 18:30:56--  https://www.dropbox.com/s/i33937mq2rs0fcm/A2C-Deterministic-v4-CnnPolicy.zip?dl=1
Resolving www.dropbox.com (www.dropbox.com)... 162.125.9.18, 2620:100:601f:18::a27d:912
Connecting to www.dropbox.com (www.dropbox.com)|162.125.9.18|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: /s/dl/i33937mq2rs0fcm/A2C-Deterministic-v4-CnnPolicy.zip [following]
--2021-03-14 18:30:56--  https://www.dropbox.com/s/dl/i33937mq2rs0fcm/A2C-Deterministic-v4-CnnPolicy.zip
Reusing existing connection to www.dropbox.com:443.
HTTP request sent, awaiting response... 302 Found
Location: https://uc89f522f6bba9cd5859f4931162.dl.dropboxusercontent.com/cd/0/get/BKqIEzqiiVHd-0dxz22Q4nGacgPS5Ci5i7_V6cMu6VwVFHMej5YpuP-ESp92hHcXP4VY3btRZau0ZyGTEvX3J5ywCJBD0-UxW9ytv2fAqsGzGFC4BxBVGRMtCXY-1Rghu6PQhLWjL7EyXu5FJxv5y3Xa/file?dl=1# [following]
--2021-03-14 18:30:56--  https://uc89f522f6bba9cd5859f4931162.dl.dropboxusercontent.com/cd/0/get/BKqIEzqiiVHd-0dxz22Q4n

Resolving ucccc483cd3cd280a898235eda53.dl.dropboxusercontent.com (ucccc483cd3cd280a898235eda53.dl.dropboxusercontent.com)... 162.125.9.15, 2620:100:601f:15::a27d:90f
Connecting to ucccc483cd3cd280a898235eda53.dl.dropboxusercontent.com (ucccc483cd3cd280a898235eda53.dl.dropboxusercontent.com)|162.125.9.15|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 27357853 (26M) [application/binary]
Saving to: ‘DQN--v4-CnnPolicy.zip’

DQN--v4-CnnPolicy.z 100%[===================>]  26.09M  71.2MB/s    in 0.4s    

2021-03-14 18:31:05 (71.2 MB/s) - ‘DQN--v4-CnnPolicy.zip’ saved [27357853/27357853]

--2021-03-14 18:31:06--  https://www.dropbox.com/s/la870jz3hq9und1/DQN-NoFrameskip-v4-CnnPolicy.zip?dl=1
Resolving www.dropbox.com (www.dropbox.com)... 162.125.9.18, 2620:100:601f:18::a27d:912
Connecting to www.dropbox.com (www.dropbox.com)|162.125.9.18|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: /s/dl/la870jz3hq9und1/DQN-NoFrameskip-

HTTP request sent, awaiting response... 302 Found
Location: https://uc88fe66444246fa82928fd6b734.dl.dropboxusercontent.com/cd/0/get/BKpr318LlObgZMST6X9hTPsfWWPII0pHs3moG9LWqMFN5GUPkprV9IyLeOpqesXOyF0dsLsefRy1UmVeyUMVVB2WvECBbEXFO_lqcwuZx7dByLNRiCsybP4is-7u_U_slNiSn2czvO8ZQ1FiFbaWbLJj/file?dl=1# [following]
--2021-03-14 18:31:16--  https://uc88fe66444246fa82928fd6b734.dl.dropboxusercontent.com/cd/0/get/BKpr318LlObgZMST6X9hTPsfWWPII0pHs3moG9LWqMFN5GUPkprV9IyLeOpqesXOyF0dsLsefRy1UmVeyUMVVB2WvECBbEXFO_lqcwuZx7dByLNRiCsybP4is-7u_U_slNiSn2czvO8ZQ1FiFbaWbLJj/file?dl=1
Resolving uc88fe66444246fa82928fd6b734.dl.dropboxusercontent.com (uc88fe66444246fa82928fd6b734.dl.dropboxusercontent.com)... 162.125.9.15, 2620:100:601f:15::a27d:90f
Connecting to uc88fe66444246fa82928fd6b734.dl.dropboxusercontent.com (uc88fe66444246fa82928fd6b734.dl.dropboxusercontent.com)|162.125.9.15|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 56759449 (54M) [application/binary]
Saving to: ‘QRDQN

Εκπαιδεύουμε τα μοντέλα DQN, A2C, PPO, QRDQN για ζητούμενα περιβάλλοντα, Deterministic-v4, -v4 και NoFrameskip-v4 και χρησιμοποιούμε την πολιτική CnnPolicy. Η λογική πίσω από την χρήση αυτής της πολιτικής και όχι του Mlp είναι στο ότι αφού έχουμε είσοδο frame η εξαγωγή των χαρακτηριστικών που παρέχουν τα Cnn μπορεί να δώσει καλύτερα αποτελέσματα

In [ ]:

types=['Deterministic-v4', '-v4', 'NoFrameskip-v4']
algorithms = ['DQN', 'A2C', 'PPO', 'QRDQN']
policies = ['CnnPolicy']
test_scores = {}

In [11]:
do_it_again = 0

if do_it_again == 1:
    for i in types:
        for j in algorithms:
            for k in policies:
                 learn_eval_save_model(j,i,k,test_scores,n_env=1,max_steps=1000000)

elif do_it_again == 0:
    A2C_Deterministic_v4 = A2C.load('A2C-Deterministic-v4-CnnPolicy', verbose = 1, learning_start = 0)
    A2C_v4 = A2C.load('A2C--v4-CnnPolicy', verbose = 1, learning_start = 0)
    A2C_NoFrameskip_v4 = A2C.load('A2C-NoFrameskip-v4-CnnPolicy', verbose = 1, learning_start = 0)
    DQN_Deterministic_v4 = DQN.load('DQN-Deterministic-v4-CnnPolicy', verbose = 1, learning_start = 0)
    DQN_v4 = DQN.load('DQN--v4-CnnPolicy', verbose = 1, learning_start = 0)
    DQN_NoFrameskip_v4 = DQN.load('DQN-NoFrameskip-v4-CnnPolicy', verbose = 1, learning_start = 0)
    PPO_Deterministic_v4 = PPO.load('PPO-Deterministic-v4-CnnPolicy', verbose = 1, learning_start = 0)
    PPO_v4 = PPO.load('PPO--v4-CnnPolicy', verbose = 1, learning_start = 0)
    PPO_NoFrameskip_v4 = PPO.load('PPO-NoFrameskip-v4-CnnPolicy', verbose = 1, learning_start = 0)
    QRDQN_Deterministic_v4 = QRDQN.load('QRDQN-Deterministic-v4-CnnPolicy', verbose = 1, learning_start = 0)
    QRDQN_v4 = QRDQN.load('QRDQN--v4-CnnPolicy', verbose = 1, learning_start = 0)
    QRDQN_NoFrameskip_v4 = QRDQN.load('QRDQN-NoFrameskip-v4-CnnPolicy', verbose = 1, learning_start = 0)

/opt/conda/lib/python3.7/site-packages/cloudpickle/cloudpickle.py:704: UserWarning: A pickle file created using an old (<=1.4.1) version of cloudpicke is currently being loaded. This is not supported by cloudpickle and will break in cloudpickle 1.7
  "will break in cloudpickle 1.7", category=UserWarning


Λόγω κακής διαχείρησης του Kaggle τα περισσότερα logs χάθηκαν επομένως γίνεται χρήση του Eval mean για την επιλογή του καλύτερου μοντέλου. Παρατηρούμε ότι τα Deterministic-v4 αποδίδουν σε γενικές γραμμές καλύτερα και ιδιαίτερα στο A2C αφού έχουμε σκορ τάξης 100 φορές μεγαλύτερο από τα άλλα δίκτυα και μεγαλύτερο ακόμα και από τα state-of-the-art models

In [15]:
all_models_name = ['A2C_Deterministic_v4', 'A2C_v4', 'A2C_NoFrameskip_v4', 'DQN_Deterministic_v4',
                   'DQN_v4', 'DQN_NoFrameskip_v4', 'PPO_Deterministic_v4', 'PPO_v4',
                   'PPO_NoFrameskip_v4', 'QRDQN_Deterministic_v4', 'QRDQN_v4', 'QRDQN_NoFrameskip_v4']
all_models = [A2C_Deterministic_v4, A2C_v4, A2C_NoFrameskip_v4, DQN_Deterministic_v4, DQN_v4,
             DQN_NoFrameskip_v4, PPO_Deterministic_v4, PPO_v4, PPO_NoFrameskip_v4,
             QRDQN_Deterministic_v4, QRDQN_v4, QRDQN_NoFrameskip_v4]

_, test_env1 = construct_enviroment('Deterministic-v4')
_, test_env2 = construct_enviroment('-v4')
_, test_env3 = construct_enviroment('NoFrameskip-v4')

test_scores = {}

for m in range(len(all_models)):
    if m%3 == 0:
        evaluate_model(all_models[m], test_env1, all_models_name[m], test_scores)
    if m%3 == 1:
        evaluate_model(all_models[m], test_env2, all_models_name[m], test_scores)
    if m%3 == 2:
        evaluate_model(all_models[m], test_env3, all_models_name[m], test_scores)
    print("Finished evaluating "+all_models_name[m]+"\n")


Eval reward: 268041.6 (+/-119.47987278198784)
Finished evaluating A2C_Deterministic_v4

Eval reward: 5765.4 (+/-283.1555049791545)
Finished evaluating A2C_v4

Eval reward: 2475.0 (+/-728.2106837996818)
Finished evaluating A2C_NoFrameskip_v4

Eval reward: 6220.8 (+/-1339.6209015986576)
Finished evaluating DQN_Deterministic_v4

Eval reward: 3656.4 (+/-460.0767762015379)
Finished evaluating DQN_v4

Eval reward: 4929.0 (+/-801.5537411802155)
Finished evaluating DQN_NoFrameskip_v4

Eval reward: 5475.6 (+/-2067.1697172704517)
Finished evaluating PPO_Deterministic_v4

Eval reward: 4190.8 (+/-446.0602649866944)
Finished evaluating PPO_v4

Eval reward: 5693.4 (+/-292.7754088034034)
Finished evaluating PPO_NoFrameskip_v4

Eval reward: 8020.2 (+/-4575.904474527413)
Finished evaluating QRDQN_Deterministic_v4

Eval reward: 5022.0 (+/-2716.6824621217697)
Finished evaluating QRDQN_v4

Eval reward: 4900.2 (+/-784.1189705650539)
Finished evaluating QRDQN_NoFrameskip_v4



#### Βελτιστοποίηση μοντέλου

Παρακάτω αλλάζουμε ελαφρά τους παραπάνω βοηθητικούς αλγορίθμους ώστε να τρέξουμε A2C μοντέλα με διαφορετικές παραμέτρους learning rate, policy και discount factor gamma

In [ ]:
def construct_rl_model_A2C(policy, rate, gamma, sde):
    
    model_name = 'A2C-Deterministic-v4-' + policy + '_' + str(rate) + 'rate_' + str(gamma) + 'gamma_sde=' + str(sde)
    time_stamp=datetime.datetime.now().strftime("-%Y%m%d-%H%M%S")
    model_log= LOG_DIR + model_name + time_stamp
    env,test_env = construct_enviroment('Deterministic-v4',n_envs = 4)
    model = A2C(policy, env, verbose=1, tensorboard_log=model_log, learning_rate = rate, gamma = gamma, use_sde = sde)
    return model,test_env, model_name

In [ ]:
def learn_eval_save_model_A2C(policy, learning_rate, gamma, sde, scores_dict, max_steps = 1000): 
    model, test_env,model_name = construct_rl_model_A2C(policy, learning_rate, gamma, sde)
    train_model = model.learn(total_timesteps=max_steps)
    print("Finished training "+model_name)
    evaluate_model(train_model,test_env, model_name,scores_dict)
    print("Finished evaluating "+model_name)
    train_model.save(model_name)
    print("Saved model:"+model_name)

In [ ]:
policies = ['MlpPolicy', 'CnnPolicy']
learning_rate = [0.0007, 0.003]
gamma = [0.99, 0.999]
use_sde = [False]
test_scores = {}
for i in use_sde:
    for j in gamma:
        for k in learning_rate:
            for l in policies:
                learn_eval_save_model_A2C(l,k,j,i,scores_dict = test_scores,max_steps=10)

Από τα αποτελέσματα βλέπουμε ότι έχουμε καλύτερα αποτελέσματα για τις παραμέτρους CnnPolicy, learning rate = 0.0007, gamma = 0.99

#### Συνέχιση Εκπαίδευσης

Το βέλτιστο μοντέλο έχει τις ίδιες παραμέτρους με αυτό το οποίο έφερε τα καλύτερα αποτελέσματα στην σύγκριση των μοντέλων διαφορετικών αρχιτεκτονικών.

Συνεχίζουμε την εκπαίδευσή του για άλλα 1000000 βήματα

In [ ]:
A2C_Deterministic_v4 = A2C.load('A2C-Deterministic-v4-CnnPolicy', verbose = 1, learning_start = 0)

env1, test_env1 = construct_enviroment('Deterministic-v4')
A2C_Deterministic_v4.set_env(env1)
train_model = A2C_Deterministic_v4.learn(total_timesteps=500000)
print("Finished training A2C-Deterministic-v4-CnnPolicy")
evaluate_model(train_model,test_env1, 'A2C-Deterministic-v4-CnnPolicy',scores_dict = {})
print("Finished evaluating "+'A2C-Deterministic-v4-CnnPolicy')
train_model.save(model_name)
print("Saved model:"+model_name)

In [ ]:
train_model = A2C_Deterministic_v4.learn(total_timesteps=500000)
print("Finished training A2C-Deterministic-v4-CnnPolicy")
evaluate_model(train_model,test_env1, 'A2C-Deterministic-v4-CnnPolicy',scores_dict = {})
print("Finished evaluating "+'A2C-Deterministic-v4-CnnPolicy')
train_model.save(model_name)
print("Saved model:"+model_name)

### Sticky Actions -v0 σε A2C μοντέλο

In [ ]:
test_scores = {}
learn_eval_save_model('A2C','Deterministic-v0','CnnPolicy',test_scores,n_env=1,max_steps=1000000)

Δεν παρατηρούμε σημαντική διαφορά για το συγκεκριμένο πλήθος βημάτων της εκπαίδευσης από την γενική απόδοση των δικτύων

### Video πράκτορα κατά την διάρκεια του παιχνιδιού 

Καταγραφή του πράκτορα για το μοντέλο A2C_Deterministic_v4 το οποίο είχε μακράν την καλύτερη επίδοση

In [9]:
!wget --no-check-certificate 'https://www.dropbox.com/s/i33937mq2rs0fcm/A2C-Deterministic-v4-CnnPolicy.zip?dl=1' -O A2C-Deterministic-v4-CnnPolicy.zip


A2C_Deterministic_v4 = A2C.load('A2C-Deterministic-v4-CnnPolicy', verbose = 1, learning_start = 0)
env1, test_env1 = construct_enviroment('Deterministic-v4')


In [7]:
!apt-get install ffmpeg freeglut3-dev xvfb  -y # For visualization
import os
os.system("Xvfb :1 -screen 0 1024x768x24 &")
os.environ['DISPLAY'] = ':1'
video_folder = '/kaggle/working/videos'
import base64
from pathlib import Path

from IPython import display as ipythondisplay

def show_videos(video_path='', prefix=''):
  """
  Taken from https://github.com/eleurent/highway-env

  :param video_path: (str) Path to the folder containing videos
  :param prefix: (str) Filter the video, showing only the only starting with this prefix
  """
  html = []
  for mp4 in Path(video_path).glob("{}*.mp4".format(prefix)):
      video_b64 = base64.b64encode(mp4.read_bytes())
      html.append('''<video alt="{}" autoplay 
                    loop controls style="height: 400px;">
                    <source src="data:video/mp4;base64,{}" type="video/mp4" />
                </video>'''.format(mp4, video_b64.decode('ascii')))
  ipythondisplay.display(ipythondisplay.HTML(data="<br>".join(html)))

import numpy as np
from stable_baselines3.common.vec_env import VecVideoRecorder, DummyVecEnv

def record_video(eval_env, model, video_length=500, prefix='', video_folder=video_folder):
  """
  :param env_id: (str)
  :param model: (RL model)
  :param video_length: (int)
  :param prefix: (str)
  :param video_folder: (str)
  """
  # Start the video at step=0 and record video_length steps
  env = VecVideoRecorder(eval_env, video_folder=video_folder,
                              record_video_trigger=lambda step: step == 0, video_length=video_length,
                              name_prefix=prefix)

  obs = env.reset()
  for _ in range(video_length):
    #action, _ = model.predict(obs)
    #θα επιλέξουμε την ενέργεια με τις μεγαλύτερες πιθανότητες
    actions, _ = model.predict(obs, deterministic=True)
    obs, _, _, _ = env.step(actions)

  # Close the video recorder
  env.close()




Reading package lists... Done
Building dependency tree       
Reading state information... Done
ffmpeg is already the newest version (7:3.4.8-0ubuntu0.2).
xvfb is already the newest version (2:1.19.6-1ubuntu4.8).
The following additional packages will be installed:
  freeglut3 libdrm-dev libegl-mesa0 libegl1 libgbm1 libgl1-mesa-dev libgles1
  libgles2 libglu1-mesa libglu1-mesa-dev libglvnd-core-dev libglvnd-dev
  libice-dev libopengl0 libpthread-stubs0-dev libsm-dev libwayland-server0
  libx11-dev libx11-doc libx11-xcb-dev libxau-dev libxcb-dri2-0-dev
  libxcb-dri3-dev libxcb-glx0-dev libxcb-present-dev libxcb-randr0
  libxcb-randr0-dev libxcb-render0-dev libxcb-shape0-dev libxcb-sync-dev
  libxcb-xfixes0-dev libxcb1-dev libxdamage-dev libxdmcp-dev libxext-dev
  libxfixes-dev libxshmfence-dev libxt-dev libxxf86vm-dev mesa-common-dev
  x11proto-core-dev x11proto-damage-dev x11proto-dev x11proto-fixes-dev
  x11proto-xext-dev x11proto-xf86vidmode-dev xorg-sgml-doctools xtrans-dev
Suggeste

Unpacking x11proto-core-dev (2018.4-4) ...
Selecting previously unselected package libxau-dev:amd64.
Preparing to unpack .../04-libxau-dev_1%3a1.0.8-1ubuntu1_amd64.deb ...
Unpacking libxau-dev:amd64 (1:1.0.8-1ubuntu1) ...
Selecting previously unselected package libxdmcp-dev:amd64.
Preparing to unpack .../05-libxdmcp-dev_1%3a1.1.2-3_amd64.deb ...
Unpacking libxdmcp-dev:amd64 (1:1.1.2-3) ...
Selecting previously unselected package xtrans-dev.
Preparing to unpack .../06-xtrans-dev_1.3.5-1_all.deb ...
Unpacking xtrans-dev (1.3.5-1) ...
Selecting previously unselected package libpthread-stubs0-dev:amd64.
Preparing to unpack .../07-libpthread-stubs0-dev_0.3-4_amd64.deb ...
Unpacking libpthread-stubs0-dev:amd64 (0.3-4) ...
Selecting previously unselected package libxcb1-dev:amd64.
Preparing to unpack .../08-libxcb1-dev_1.13-2~ubuntu18.04_amd64.deb ...
Unpacking libxcb1-dev:amd64 (1.13-2~ubuntu18.04) ...
Selecting previously unselected package libx11-dev:amd64.
Preparing to unpack .../09-libx1

Setting up libopengl0:amd64 (1.0.0-2ubuntu2.3) ...
Setting up freeglut3:amd64 (2.8.1-3) ...
Setting up libgles1:amd64 (1.0.0-2ubuntu2.3) ...
Setting up libxcb-randr0:amd64 (1.13-2~ubuntu18.04) ...
Setting up libxshmfence-dev:amd64 (1.3-1) ...
Setting up libpthread-stubs0-dev:amd64 (0.3-4) ...
Setting up libdrm-dev:amd64 (2.4.101-2~18.04.1) ...
Setting up xorg-sgml-doctools (1:1.11-1) ...
Setting up x11proto-dev (2018.4-4) ...
Setting up x11proto-damage-dev (1:2018.4-4) ...
Setting up xtrans-dev (1.3.5-1) ...
Setting up x11proto-xext-dev (2018.4-4) ...
Setting up libxdmcp-dev:amd64 (1:1.1.2-3) ...
Setting up libice-dev:amd64 (2:1.0.9-2) ...
Setting up libx11-doc (2:1.6.4-3ubuntu0.3) ...
Setting up libgles2:amd64 (1.0.0-2ubuntu2.3) ...
Setting up libglu1-mesa:amd64 (9.0.0-2.1build1) ...
Setting up libglvnd-core-dev:amd64 (1.0.0-2ubuntu2.3) ...
Setting up libwayland-server0:amd64 (1.16.0-1ubuntu1.1~18.04.3) ...
Setting up libsm-dev:amd64 (2:1.2.2-1) ...
Setting up x11proto-core-dev (2018.

In [10]:
record_video(test_env1, A2C_Deterministic_v4, video_length=10000, prefix='A2C')
show_videos(video_path = video_folder, prefix='A2C')

Saving video to  /kaggle/working/videos/A2C-step-0-to-step-10000.mp4
